Import necessary modules 

In [1]:
import os, io, requests
import numpy as np
import pandas as pd

The fallowing is included so that the tables appear cleaner when exporting to pdf

In [2]:
pd.set_option('display.notebook_repr_html', True)

def _repr_latex_(self):
    return "\centering{%s}" % self.to_latex()

pd.DataFrame._repr_latex_ = _repr_latex_  # monkey patch pandas DataFrame

All data was aquired from The Human Protein Atlas (THPA) (http://www.proteinatlas.org/).   
The data was downloaded on 1/18/2016.   
The following is the necessary link to the download page for the data: http://www.proteinatlas.org/about/download

The following generates gene-tissue set libraries and tissue-gene set libraries for the Normal Tissue Data form THPA.    

Values were neglected only if labeled 'Not Detected.'  

Here is the description of the orginal data from the THPA website:  
Expression profiles for proteins in human tissues based on immunohistochemisty using tissue micro arrays.
The data is based on The Human Protein Atlas version 16 and Ensembl version 83.38.

55 unique tissues reported  
12978 unique genes reported

The link to the data is found here: http://www.proteinatlas.org/download/normal_tissue.csv.zip

In [3]:
normal_tissue_protein = pd.read_csv('Data/normal_tissue.csv.zip', sep=',')

In [4]:
normal_tissue_protein = normal_tissue_protein[normal_tissue_protein['Level'] != 'Not detected']

In [5]:
gene_tissue_lib = pd.DataFrame()

i = 0




for gene in normal_tissue_protein['Gene name'].unique().tolist():
    lst = []
    i += 1
    print('\r'+ str(i) + ' Out of ' + str(len(normal_tissue_protein['Gene name'].unique().tolist())), end='', flush=True)
    
    lst1 = normal_tissue_protein[normal_tissue_protein['Gene name'] == gene]['Tissue'].values.tolist()
    lst2 = normal_tissue_protein[normal_tissue_protein['Gene name'] == gene]['Cell type'].values.tolist()
    
    lst = list("%s-%s" % t for t in zip(lst1, lst2))
    
    lst.insert(0, gene)
    temp = pd.DataFrame(data=lst)
    gene_tissue_lib = pd.concat([gene_tissue_lib, temp.T])

gene_tissue_lib.to_csv('Output/gene_tissue_lib.gmt', sep='\t', header=False, index=False)

12843 Out of 12843

# (1)

In [6]:
gene_tissue_lib.head()

0                                1                                2    \
0    TSPAN6         appendix-glandular cells           breast-glandular cells   
0      DPM1    adrenal gland-glandular cells         appendix-glandular cells   
0     SCYL3         appendix-glandular cells  bone marrow-hematopoietic cells   
0  C1orf112    adrenal gland-glandular cells         appendix-lymphoid tissue   
0       FGR  bone marrow-hematopoietic cells                 lung-macrophages   

                                     3    \
0  bronchus-respiratory epithelial cells   
0               appendix-lymphoid tissue   
0                      breast-adipocytes   
0        bone marrow-hematopoietic cells   
0       lymph node-germinal center cells   

                                    4                                5    \
0        cerebral cortex-neuronal cells  cervix, uterine-glandular cells   
0       bone marrow-hematopoietic cells                breast-adipocytes   
0                breast-glandular cells       breast-myoepithelial cells   
0                     breast-adipocytes           breast-glandular cells   
0  lymph node-non-germinal center cells         spleen-cells in red pulp   

                                         6    \
0  cervix, uterine-squamous epithelial cells   
0                     breast-glandular cells   
0                  cerebellum-Purkinje cells   
0                 breast-myoepithelial cells   
0               tonsil-germinal center cells   

                                     7    \
0                  colon-glandular cells   
0             breast-myoepithelial cells   
0      cerebral cortex-endothelial cells   
0  bronchus-respiratory epithelial cells   
0       tonsil-non-germinal center cells   

                                     8                               9   ...   \
0               duodenum-glandular cells   endometrium 1-glandular cells ...    
0  bronchus-respiratory epithelial cells             caudate-glial cells ...    
0            cerebral cortex-glial cells  cerebral cortex-neuronal cells ...    
0                    caudate-glial cells          caudate-neuronal cells ...    
0       tonsil-squamous epithelial cells                             NaN ...    

   143  144  145  146  147  148  149  150  151  152  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  

[5 rows x 153 columns]

In [7]:
normal_tissue_protein = normal_tissue_protein.sort_values(['Tissue', 'Cell type'])

In [8]:
tissue_gene_lib = pd.DataFrame()

i = 0

tissue_set = ["%s-%s" % t for t in zip(normal_tissue_protein['Tissue'].unique().tolist(), normal_tissue_protein['Cell type'].unique().tolist())]



for tissue in tissue_set:
    lst = []
    i += 1
    print('\r'+ str(i) + ' Out of ' + str(len(normal_tissue_protein['Tissue'].unique().tolist())), end='', flush=True)
    
    lst = normal_tissue_protein[normal_tissue_protein['Tissue'] == tissue.split('-')[0]]['Gene name'].values.tolist()
    
    lst.insert(0, tissue)
    temp = pd.DataFrame(data=lst)
    tissue_gene_lib = pd.concat([tissue_gene_lib, temp.T])

tissue_gene_lib.to_csv('Output/tissue_gene_lib.gmt', sep='\t', header=False, index=False)

55 Out of 55

# (2)

In [9]:
tissue_gene_lib.head()

0       1       2         3      4      \
0  adrenal gland-cells in zona fasciculata  ELOVL5  AKR1B1       RGN    NOV   
0       appendix-cells in zona glomerulosa  TSPAN6    DPM1     SCYL3  FUCA2   
0    bone marrow-cells in zona reticularis    DPM1   SCYL3  C1orf112    FGR   
0                   breast-glandular cells    DPM1   SCYL3  C1orf112  LAS1L   
0                 bronchus-medullary cells  TSPAN6    DPM1  C1orf112  FUCA2   

    5       6        7       8        9      ...  26708 26709 26710 26711  \
0   MGARP    FDX1  CYP11A1    STAR  CYP17A1  ...    NaN   NaN   NaN   NaN   
0    GCLC    NFYA   NIPAL3   LAS1L    ENPP4  ...    NaN   NaN   NaN   NaN   
0   FUCA2    GCLC     NFYA  NIPAL3    LAS1L  ...    NaN   NaN   NaN   NaN   
0  SEMA3F  ANKIB1     LAP3   HECW1   MAD1L1  ...    NaN   NaN   NaN   NaN   
0    GCLC    NFYA   NIPAL3   LAS1L    ENPP4  ...    NaN   NaN   NaN   NaN   

  26712 26713 26714 26715 26716 26717  
0   NaN   NaN   NaN   NaN   NaN   NaN  
0   NaN   NaN   NaN   NaN   NaN   NaN  
0   NaN   NaN   NaN   NaN   NaN   NaN  
0   NaN   NaN   NaN   NaN   NaN   NaN  
0   NaN   NaN   NaN   NaN   NaN   NaN  

[5 rows x 26718 columns]

The following generates gene-cancer set libraries and cancer-gene set libraries for the Normal Tissue Data form THPA.    

Values were neglected only if all are found to be 'Not Detected.'  

Here is the description of the orginal data from the THPA website:  
Staining profiles for proteins in human tumor tissue based on immunohistochemisty using tissue micro arrays. 
The data is based on The Human Protein Atlas version 16 and Ensembl version 83.38. 

20 cancer type reported  
15288 genes reported

The link to the data is found here:http://www.proteinatlas.org/download/cancer.csv.zip

In [10]:
cancer_data = pd.read_csv('Data/cancer.csv.zip', sep=',')

In [12]:
cancer_data = cancer_data[3::4]# extract only the not detected entries (dont need the repeat of Tumor for each level)
cancer_data = cancer_data[cancer_data['Count patients'] != cancer_data['Total patients']]#discard non-detected values

gene_cancer_lib = pd.DataFrame()

i = 0

lst = []

for gene in cancer_data['Gene name'].unique().tolist():
    i += 1
    print('\r'+ str(i) + ' Out of ' + str(len(cancer_data['Gene name'].unique().tolist())), end='', flush=True)
    lst = cancer_data[cancer_data['Gene name'] == gene]['Tumor'].values.tolist()
    lst.insert(0, gene)
    temp = pd.DataFrame(data=lst)
    gene_cancer_lib = pd.concat([gene_cancer_lib, temp.T])

gene_cancer_lib.to_csv('Output/gene_cancer_lib.gmt', sep='\t', header=False, index=False)

14891 Out of 14891

# (3)

In [13]:
gene_cancer_lib.head()

0              1          2                3                  4   \
0    TSPAN6  breast cancer  carcinoid  cervical cancer  colorectal cancer   
0      TNMD  breast cancer  carcinoid  cervical cancer  colorectal cancer   
0      DPM1  breast cancer  carcinoid  cervical cancer  colorectal cancer   
0     SCYL3  breast cancer  carcinoid  cervical cancer  colorectal cancer   
0  C1orf112  breast cancer  carcinoid  cervical cancer  colorectal cancer   

                   5                     6                     7   \
0  endometrial cancer  head and neck cancer          liver cancer   
0  endometrial cancer                glioma  head and neck cancer   
0  endometrial cancer                glioma  head and neck cancer   
0  endometrial cancer                glioma  head and neck cancer   
0  endometrial cancer                glioma  head and neck cancer   

             8            9  ...    31   32   33   34   35   36   37   38  \
0   lung cancer     melanoma ...   NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
0  liver cancer  lung cancer ...   NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
0  liver cancer  lung cancer ...   NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
0  liver cancer  lung cancer ...   NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
0  liver cancer  lung cancer ...   NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   

    39   40  
0  NaN  NaN  
0  NaN  NaN  
0  NaN  NaN  
0  NaN  NaN  
0  NaN  NaN  

[5 rows x 41 columns]

In [14]:
cancer_data = cancer_data.sort_values('Tumor')

cancer_gene_lib = pd.DataFrame()

i = 0

lst = []

for cancer in cancer_data['Tumor'].unique().tolist():
    i += 1
    print('\r'+ str(i) + ' Out of ' + str(len(cancer_data['Tumor'].unique().tolist())), end='', flush=True)
    lst = cancer_data[cancer_data['Tumor'] == cancer]['Gene name'].values.tolist()
    lst.insert(0, cancer)
    temp = pd.DataFrame(data=lst)
    cancer_gene_lib = pd.concat([cancer_gene_lib, temp.T])
    
cancer_gene_lib.to_csv('Output/cancer_gene_lib.gmt', sep='\t', header=False, index=False)

20 Out of 20

# (4)

In [15]:
cancer_gene_lib.head()

0        1        2        3       4       5        6      \
0       breast cancer   TSPAN6   GTF2H3  ARHGDIB  PPP1CC  RASAL1      MGP   
0           carcinoid  CAMSAP1  PHYHIPL  HEPACAM   CRHBP  ATXN10     ABRA   
0     cervical cancer    IFNB1     SELL    RHOT2  GOLGA2    GPD1    MAPK9   
0   colorectal cancer     GRB2  APOBEC2   FAM83H    PDCL  ZNF431     OAZ1   
0  endometrial cancer    WDR24    ABHD3    SNX10   GORAB  CREBBP  METTL25   

      7      8             9      ...  12983 12984 12985 12986 12987 12988  \
0    ZNF555   OAS2       PRELID2  ...    NaN   NaN   NaN   NaN   NaN   NaN   
0     TBL1Y  PCSK2          ISPD  ...    NaN   NaN   NaN   NaN   NaN   NaN   
0     PFDN4  TRUB2         NKPD1  ...    NaN   NaN   NaN   NaN   NaN   NaN   
0    KANSL3  DYDC1  RP13-582O9.6  ...    NaN   NaN   NaN   NaN   NaN   NaN   
0  TBC1D22B   ANO9       ZMYM6NB  ...    NaN   NaN   NaN   NaN   NaN   NaN   

  12989 12990 12991 12992  
0   NaN   NaN   NaN   NaN  
0   NaN   NaN   NaN   NaN  
0   NaN   NaN   NaN   NaN  
0   NaN   NaN   NaN   NaN  
0   NaN   NaN   NaN   NaN  

[5 rows x 12993 columns]

The following generates gene-tissue up and down set libraries for genes that are up regulated and down regulated, respectively, as well as, tissue-gene up and down set libraries for the Normal Tissue Data form THPA.    

Values were normalized using z-score nomalization, per gene values.  

Here is the description of the orginal data from the THPA website:  
RNA levels in 37 tissues based on RNA-seq. The comma-separated file includes Ensembl gene identifier ("Gene"), analysed sample ("Sample") and fragments per kilobase of transcript per million fragments mapped ("Value" and "Unit"). The data is based on The Human Protein Atlas version 16 and Ensembl version 83.38.   

The link to the data is found here: http://www.proteinatlas.org/download/rna_tissue.csv.zip

In [16]:
rna_tissue = pd.read_csv('Data/rna_tissue.csv.zip', sep=',')

z-score nomalization accross each gene

In [17]:
i = 0
master_list = []
for gene in rna_tissue['Gene name'].unique():
    lst = rna_tissue[rna_tissue['Gene name'] == gene].Value.values
    lst = (lst-lst.mean())/(lst.std())
    master_list.extend(lst)
    i += 1
    print('\r'+ str(i) + ' Out of ' + str(len(rna_tissue['Gene name'].unique())), end='', flush=True)
rna_tissue.Value = master_list    

1899 Out of 19610

/Users/moshesilverstein/anaconda/lib/python3.5/site-packages/ipykernel/__main__.py:5: RuntimeWarning: invalid value encountered in true_divide


19610 Out of 19610

Gene-Tissue up (regulated) library

In [18]:
up_rna_tissue = rna_tissue[rna_tissue['Value'] > 0]

rna_gene_tissue_lib_up = pd.DataFrame()

i = 0

lst = []

for gene in up_rna_tissue['Gene name'].unique().tolist():
    i += 1
    print('\r'+ str(i) + ' Out of ' + str(len(up_rna_tissue['Gene name'].unique().tolist())), end='', flush=True)
    lst = up_rna_tissue[up_rna_tissue['Gene name'] == gene]['Sample'].values.tolist()
    lst.insert(0, gene)
    temp = pd.DataFrame(data=lst)
    rna_gene_tissue_lib_up = pd.concat([rna_gene_tissue_lib_up, temp.T])
    
rna_gene_tissue_lib_up.dropna(thresh=2, axis=0, inplace=True)

rna_gene_tissue_lib_up.to_csv('Output/rna_gene_tissue_lib_up.gmt', sep='\t', header=False, index=False)

19176 Out of 19176

# (5)

In [19]:
rna_gene_tissue_lib_up.head()

0               1                2                3            4   \
0    TSPAN6          breast  cervix, uterine            colon  endometrium   
0      TNMD  adipose tissue           breast            ovary     placenta   
0      DPM1   adrenal gland         appendix           breast  endometrium   
0     SCYL3        appendix           breast  cervix, uterine  endometrium   
0  C1orf112        appendix      bone marrow      endometrium   lymph node   

                  5                6               7            8   \
0          esophagus   fallopian tube     gallbladder       kidney   
0           prostate  seminal vesicle             NaN          NaN   
0         epididymis        esophagus  fallopian tube  gallbladder   
0         epididymis   fallopian tube     gallbladder   lymph node   
0  parathyroid gland         placenta          rectum       testis   

                  9  ...    25   26   27   28   29   30   31   32   33   34  
0              liver ...   NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0                NaN ...   NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0             kidney ...   NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  parathyroid gland ...   NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0             tonsil ...   NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  

[5 rows x 35 columns]

Gene-Tissue down (regulated) library

In [20]:
dn_rna_tissue = rna_tissue[rna_tissue['Value'] < 0]

rna_gene_tissue_lib_dn = pd.DataFrame()

i = 0

lst = []

for gene in dn_rna_tissue['Gene name'].unique().tolist():
    i += 1
    print('\r'+ str(i) + ' Out of ' + str(len(dn_rna_tissue['Gene name'].unique().tolist())), end='', flush=True)
    lst = dn_rna_tissue[dn_rna_tissue['Gene name'] == gene]['Sample'].values.tolist()
    lst.insert(0, gene)
    temp = pd.DataFrame(data=lst)
    rna_gene_tissue_lib_dn = pd.concat([rna_gene_tissue_lib_dn, temp.T])
    
rna_gene_tissue_lib_dn.dropna(thresh=2, axis=0, inplace=True)

rna_gene_tissue_lib_dn.to_csv('Output/rna_gene_tissue_lib_dn.gmt', sep='\t', header=False, index=False)

19181 Out of 19181

# (6)

In [21]:
rna_gene_tissue_lib_dn.head()

0               1              2                3                4   \
0    TSPAN6  adipose tissue  adrenal gland         appendix      bone marrow   
0      TNMD   adrenal gland       appendix      bone marrow  cerebral cortex   
0      DPM1  adipose tissue    bone marrow  cerebral cortex  cervix, uterine   
0     SCYL3  adipose tissue  adrenal gland      bone marrow  cerebral cortex   
0  C1orf112  adipose tissue  adrenal gland           breast  cerebral cortex   

                5         6             7             8           9  ...   \
0  cerebral cortex  duodenum    epididymis  heart muscle        lung ...    
0  cervix, uterine     colon      duodenum   endometrium  epididymis ...    
0            colon  duodenum  heart muscle         liver        lung ...    
0            colon  duodenum     esophagus  heart muscle      kidney ...    
0  cervix, uterine     colon      duodenum    epididymis   esophagus ...    

    56   57   58   59   60   61   62   63   64   65  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  

[5 rows x 66 columns]

Tissue-Gene up (regulated) library

In [23]:
up_rna_tissue = rna_tissue[rna_tissue['Value'] > 0]

rna_tissue_gene_lib_up = pd.DataFrame()

i = 0

lst = []

for tissue in up_rna_tissue['Sample'].unique().tolist():
    i += 1
    print('\r'+ str(i) + ' Out of ' + str(len(up_rna_tissue['Sample'].unique().tolist())), end='', flush=True)
    lst = up_rna_tissue[up_rna_tissue['Sample'] == tissue]['Gene name'].values.tolist()
    lst.insert(0, tissue)
    temp = pd.DataFrame(data=lst)
    rna_tissue_gene_lib_up = pd.concat([rna_tissue_gene_lib_up, temp.T])
    
rna_tissue_gene_lib_up.dropna(thresh=2, axis=0, inplace=True)

rna_tissue_gene_lib_up.to_csv('Output/rna_tissue_gene_lib_up.gmt', sep='\t', header=False, index=False)

37 Out of 37

# (7)

In [24]:
rna_tissue_gene_lib_up.head()

0       1      2      3         4        5       6      7      \
0           breast  TSPAN6   TNMD   DPM1     SCYL3      CFH    GCLC   NFYA   
0  cervix, uterine  TSPAN6  SCYL3    CFH     FUCA2     NFYA   LAS1L  ENPP4   
0            colon  TSPAN6  FUCA2  STPG1      CFTR  CYP51A1   RAD52    BAD   
0      endometrium  TSPAN6   DPM1  SCYL3  C1orf112    FUCA2    GCLC   NFYA   
0        esophagus  TSPAN6   DPM1   GCLC    SEMA3F     CD99  HS3ST1  HECW1   

    8        9      ...  10816 10817 10818 10819 10820 10821 10822 10823  \
0   LAS1L  CYP51A1  ...    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
0  SEMA3F     CFTR  ...    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
0    AOC1    LASP1  ...    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
0   LAS1L   ANKIB1  ...    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
0  MAD1L1    SNX11  ...    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   

  10824 10825  
0   NaN   NaN  
0   NaN   NaN  
0   NaN   NaN  
0   NaN   NaN  
0   NaN   NaN  

[5 rows x 10826 columns]

Tissue-Gene down (regulated) library

In [26]:
dn_rna_tissue = rna_tissue[rna_tissue['Value'] < 0]

rna_tissue_gene_lib_dn = pd.DataFrame()

i = 0

lst = []

for tissue in dn_rna_tissue['Sample'].unique().tolist():
    i += 1
    print('\r'+ str(i) + ' Out of ' + str(len(dn_rna_tissue['Sample'].unique().tolist())), end='', flush=True)
    lst = dn_rna_tissue[dn_rna_tissue['Sample'] == tissue]['Gene name'].values.tolist()
    lst.insert(0, tissue)
    temp = pd.DataFrame(data=lst)
    rna_tissue_gene_lib_dn = pd.concat([rna_tissue_gene_lib_dn, temp.T])
    
rna_tissue_gene_lib_dn.dropna(thresh=2, axis=0, inplace=True)

rna_tissue_gene_lib_dn.to_csv('Output/rna_tissue_gene_lib_dn.gmt', sep='\t', header=False, index=False)

37 Out of 37

# (8)

In [27]:
rna_tissue_gene_lib_dn.head()

0       1     2      3         4         5      6       7      \
0   adipose tissue  TSPAN6  DPM1  SCYL3  C1orf112     FUCA2   NFYA   STPG1   
0    adrenal gland  TSPAN6  TNMD  SCYL3  C1orf112       FGR    CFH    GCLC   
0         appendix  TSPAN6  TNMD    CFH     FUCA2      GCLC  STPG1  NIPAL3   
0      bone marrow  TSPAN6  TNMD   DPM1     SCYL3       CFH  FUCA2    GCLC   
0  cerebral cortex  TSPAN6  TNMD   DPM1     SCYL3  C1orf112    FGR     CFH   

    8       9      ...  18883 18884 18885 18886 18887 18888 18889 18890 18891  \
0  NIPAL3   LAS1L  ...    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
0    NFYA   STPG1  ...    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
0   ENPP4  SEMA3F  ...    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
0   STPG1  NIPAL3  ...    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
0   FUCA2  SEMA3F  ...    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   

  18892  
0   NaN  
0   NaN  
0   NaN  
0   NaN  
0   NaN  

[5 rows x 18893 columns]

The following generates gene-celline up and down set libraries for genes that are up regulated and down regulated, respectively, as well as, celline-gene up and down set libraries for the Normal Tissue Data form THPA.    

Values were normalized using z-score nomalization, per gene values.  

Here is the description of the orginal data from the THPA website:  
RNA levels in 56 cell lines based on RNA-seq. The comma-separated file includes Ensembl gene identifier ("Gene"), analysed sample ("Sample") and fragments per kilobase of transcript per million fragments mapped ("Value" and "Unit"). The data is based on The Human Protein Atlas version 16 and Ensembl version 83.38.   

The link to the data is found here: http://www.proteinatlas.org/download/rna_celline.csv.zip

In [28]:
rna_celline = pd.read_csv('Data/rna_celline.csv.zip', sep=',')

z-score nomalization accross each gene

In [29]:
i = 0
master_list = []
for gene in rna_celline['Gene name'].unique():
    lst = rna_celline[rna_celline['Gene name'] == gene].Value.values
    lst = (lst-lst.mean())/(lst.std())
    master_list.extend(lst)
    i += 1
    print('\r'+ str(i) + ' Out of ' + str(len(rna_celline['Gene name'].unique())), end='', flush=True)
rna_celline.Value = master_list  

124 Out of 19610

/Users/moshesilverstein/anaconda/lib/python3.5/site-packages/ipykernel/__main__.py:5: RuntimeWarning: invalid value encountered in true_divide


19610 Out of 19610

Gene-Celline up (regulated) library

In [30]:
up_rna_celline = rna_celline[rna_celline['Value'] > 0]

rna_gene_celline_lib_up = pd.DataFrame()

i = 0

lst = []

for gene in up_rna_celline['Gene name'].unique().tolist():
    i += 1
    print('\r'+ str(i) + ' Out of ' + str(len(up_rna_celline['Gene name'].unique().tolist())), end='', flush=True)
    lst = up_rna_celline[up_rna_celline['Gene name'] == gene]['Sample'].values.tolist()
    lst.insert(0, gene)
    temp = pd.DataFrame(data=lst)
    rna_gene_celline_lib_up = pd.concat([rna_gene_celline_lib_up, temp.T])
    
rna_gene_celline_lib_up.dropna(thresh=2, axis=0, inplace=True)

rna_gene_celline_lib_up.to_csv('Output/rna_gene_celline_lib_up.gmt', sep='\t', header=False, index=False)

18879 Out of 18879

# (9)

In [31]:
rna_gene_celline_lib_up.head()

0        1                        2          3   \
0    TSPAN6     A549                     AF22     AN3-CA   
0      TNMD  NTERA-2                      NaN        NaN   
0      DPM1    A-431  BJ hTERT+ SV40 Large T+     CACO-2   
0     SCYL3     AF22                     BEWO  BJ hTERT+   
0  C1orf112    A-431                     AF22       BEWO   

                        4                                5   \
0                     BEWO          BJ hTERT+ SV40 Large T+   
0                      NaN                              NaN   
0                  CAPAN-2                           EFO-21   
0  BJ hTERT+ SV40 Large T+  BJ hTERT+ SV40 Large T+ RasG12V   
0  BJ hTERT+ SV40 Large T+  BJ hTERT+ SV40 Large T+ RasG12V   

                                6           7           8           9  ...   \
0  BJ hTERT+ SV40 Large T+ RasG12V      CACO-2     CAPAN-2      EFO-21 ...    
0                              NaN         NaN         NaN         NaN ...    
0                            HaCaT  HBF TERT88      Hep G2       HL-60 ...    
0                          CAPAN-2       HaCaT  HBF TERT88      HDLM-2 ...    
0                          CAPAN-2       Daudi       HaCaT  HBF TERT88 ...    

    44   45   46   47   48   49   50   51   52   53  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  

[5 rows x 54 columns]

Gene-Celline down (regulated) library

In [32]:
dn_rna_celline = rna_celline[rna_celline['Value'] < 0]

rna_gene_celline_lib_dn = pd.DataFrame()

i = 0

lst = []

for gene in dn_rna_celline['Gene name'].unique().tolist():
    i += 1
    print('\r'+ str(i) + ' Out of ' + str(len(dn_rna_celline['Gene name'].unique().tolist())), end='', flush=True)
    lst = dn_rna_celline[dn_rna_celline['Gene name'] == gene]['Sample'].values.tolist()
    lst.insert(0, gene)
    temp = pd.DataFrame(data=lst)
    rna_gene_celline_lib_dn = pd.concat([rna_gene_celline_lib_dn, temp.T])
    
rna_gene_celline_lib_dn.dropna(thresh=2, axis=0, inplace=True)

rna_gene_celline_lib_dn.to_csv('Output/rna_gene_celline_lib_dn.gmt', sep='\t', header=False, index=False)

18882 Out of 18882

# (10)

In [33]:
rna_gene_celline_lib_dn.head()

0      1          2          3          4          5       6    \
0    TSPAN6  A-431  ASC TERT1         BJ  BJ hTERT+      Daudi   HaCaT   
0      TNMD  A-431       A549       AF22     AN3-CA  ASC TERT1    BEWO   
0      DPM1   A549       AF22     AN3-CA  ASC TERT1       BEWO      BJ   
0     SCYL3  A-431       A549     AN3-CA  ASC TERT1         BJ  CACO-2   
0  C1orf112   A549     AN3-CA  ASC TERT1         BJ  BJ hTERT+  CACO-2   

         7                                8                        9   ...   \
0     HDLM-2                              HEL                     HeLa ...    
0         BJ                        BJ hTERT+  BJ hTERT+ SV40 Large T+ ...    
0  BJ hTERT+  BJ hTERT+ SV40 Large T+ RasG12V                    Daudi ...    
0      Daudi                           EFO-21                  HEK 293 ...    
0     EFO-21                           HDLM-2                  HEK 293 ...    

   94   95   96   97   98   99   100  101  102  103  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  

[5 rows x 104 columns]

Celline-Gene up (regulated) library

In [34]:
up_rna_celline = rna_celline[rna_celline['Value'] > 0]

rna_celline_gene_lib_up = pd.DataFrame()

i = 0

lst = []

for celline in up_rna_celline['Sample'].unique().tolist():
    i += 1
    print('\r'+ str(i) + ' Out of ' + str(len(up_rna_celline['Sample'].unique().tolist())), end='', flush=True)
    lst = up_rna_celline[up_rna_celline['Sample'] == celline]['Gene name'].values.tolist()
    lst.insert(0, celline)
    temp = pd.DataFrame(data=lst)
    rna_celline_gene_lib_up = pd.concat([rna_celline_gene_lib_up, temp.T])
    
rna_celline_gene_lib_up.dropna(thresh=2, axis=0, inplace=True)

rna_celline_gene_lib_up.to_csv('Output/rna_celline_gene_lib_up.gmt', sep='\t', header=False, index=False)

56 Out of 56

# (11)

In [35]:
rna_celline_gene_lib_up.head()

0       1      2         3         4        5     \
0                     A549  TSPAN6    CFH      GCLC     LAS1L    RAD52   
0                     AF22  TSPAN6  SCYL3  C1orf112      NFYA  CYP51A1   
0                   AN3-CA  TSPAN6  FUCA2      GCLC      NFYA    STPG1   
0                     BEWO  TSPAN6  SCYL3  C1orf112     FUCA2    RAD52   
0  BJ hTERT+ SV40 Large T+  TSPAN6   DPM1     SCYL3  C1orf112    FUCA2   

     6        7       8        9    ...  8777 8778 8779 8780 8781 8782 8783  \
0     BAD     CD99   HECW1    LASP1 ...   NaN  NaN  NaN  NaN  NaN  NaN  NaN   
0   KRIT1    RAD52    CD99   HS3ST1 ...   NaN  NaN  NaN  NaN  NaN  NaN  NaN   
0  ANKIB1  CYP51A1   KRIT1    RAD52 ...   NaN  NaN  NaN  NaN  NaN  NaN  NaN   
0   LASP1    SNX11    M6PR  CYP26B1 ...   NaN  NaN  NaN  NaN  NaN  NaN  NaN   
0    NFYA    STPG1  NIPAL3    LAS1L ...   NaN  NaN  NaN  NaN  NaN  NaN  NaN   

  8784 8785 8786  
0  NaN  NaN  NaN  
0  NaN  NaN  NaN  
0  NaN  NaN  NaN  
0  NaN  NaN  NaN  
0  NaN  NaN  NaN  

[5 rows x 8787 columns]

Celline-Gene down (egulated) library

In [36]:
dn_rna_celline = rna_celline[rna_celline['Value'] < 0]

rna_celline_gene_lib_dn = pd.DataFrame()

i = 0

lst = []

for celline in dn_rna_celline['Sample'].unique().tolist():
    i += 1
    print('\r'+ str(i) + ' Out of ' + str(len(dn_rna_celline['Sample'].unique().tolist())), end='', flush=True)
    lst = dn_rna_celline[dn_rna_celline['Sample'] == celline]['Gene name'].values.tolist()
    lst.insert(0, celline)
    temp = pd.DataFrame(data=lst)
    rna_celline_gene_lib_dn = pd.concat([rna_celline_gene_lib_dn, temp.T])
    
rna_celline_gene_lib_dn.dropna(thresh=2, axis=0, inplace=True)

rna_celline_gene_lib_dn.to_csv('Output/rna_celline_gene_lib_dn.gmt', sep='\t', header=False, index=False)

56 Out of 56

# (12)

In [37]:
rna_celline_gene_lib_dn.head()

0       1     2      3         4         5      6      7       8      \
0      A-431  TSPAN6  TNMD  SCYL3       FGR       CFH   NFYA  ENPP4  SEMA3F   
0  ASC TERT1  TSPAN6  TNMD   DPM1     SCYL3  C1orf112    FGR   GCLC    NFYA   
0         BJ  TSPAN6  TNMD   DPM1     SCYL3  C1orf112    FGR   GCLC    NFYA   
0  BJ hTERT+  TSPAN6  TNMD   DPM1  C1orf112       FGR   GCLC   NFYA   LAS1L   
0      Daudi  TSPAN6  TNMD   DPM1     SCYL3       CFH  FUCA2   NFYA   STPG1   

    9      ...  15648 15649 15650 15651 15652 15653 15654 15655 15656 15657  
0    CFTR  ...    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
0  NIPAL3  ...    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
0   LAS1L  ...    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
0   ENPP4  ...    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
0  NIPAL3  ...    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  

[5 rows x 15658 columns]

The following loads and displays the version information  
From J.R. Johansson (jrjohansson at gmail.com)

In [38]:
%load_ext version_information

%version_information numpy, matplotlib, version_information

Software versions
Python 3.5.2 64bit [GCC 4.2.1 Compatible Apple LLVM 4.2 (clang-425.0.28)]
IPython 5.1.0
OS Darwin 14.5.0 x86_64 i386 64bit
numpy 1.11.2
matplotlib 1.5.3
version_information 1.0.3
Mon Jan 23 10:16:26 2017 EST